# Course 09 Machine learning Capestone project

## Week 05: Final Project

### Segmenting and Clustering Neighborhoods in NYC and allocating similar neighborhoods for Downtown, Brooklyn for selecting best location for Bakery shop branch

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in New York City</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    

6. <a href="#item6">Final Result</a>    

</font>
</div>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import math # library for math calculations

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


c:\python27\lib\site-packages\folium\__init__.py:59: UserWarning: This version of folium is the last to support Python 2. Transition to Python 3 to be able to receive updates and fixes. Check out https://python3statement.org/ for more info.
  UserWarning


<a id='item1'></a>

## 1. Download and Explore Dataset

Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood. 

Luckily, this dataset exists for free on the web. Feel free to try to find this dataset on your own, but here is the link to the dataset: https://geo.nyu.edu/catalog/nyu_2451_34572

For your convenience, I downloaded the files and placed it on the server, so you can simply run a `wget` command and access the data. So let's go ahead and do that.

#### Load and explore the data

Next, let's load the data.

In [2]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Let's take a quick look at the data.

Notice how all the relevant data is in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [3]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.

In [4]:
neighborhoods_data[0]

{u'geometry': {u'coordinates': [-73.84720052054902, 40.89470517661],
  u'type': u'Point'},
 u'geometry_name': u'geom',
 u'id': u'nyu_2451_34572.1',
 u'properties': {u'annoangle': 0.0,
  u'annoline1': u'Wakefield',
  u'annoline2': None,
  u'annoline3': None,
  u'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661],
  u'borough': u'Bronx',
  u'name': u'Wakefield',
  u'stacked': 1},
 u'type': u'Feature'}

#### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [5]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [6]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [7]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [8]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.

In [9]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


And make sure that our dataset has Downtown neighborhood in Brooklyn Borough.

In [10]:
for idx, val in enumerate(neighborhoods_data):
    if val['properties']['name'].startswith('Downtown'):
        print(idx, val['properties']['borough'])
        Downtown_lat = val['geometry']['coordinates'][1]
        Downtown_long = val['geometry']['coordinates'][0]

(86, u'Brooklyn')


#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [11]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [12]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  

folium.Marker([Downtown_lat, Downtown_long], popup='Downtown, Brooklyn', icon=folium.Icon(color='red')).add_to(map_newyork)      

map_newyork

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [13]:
CLIENT_ID = 'RH2TN4WWZYPCFZ3SWLLPJUECHOYUBPGFCL05JVGXPIBEMMNT' # your Foursquare ID
CLIENT_SECRET = 'ZMCVBIQCF0110IUVFTSD4BIJCE43M4GSA21ZKSSMH3X0YH3K' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [14]:
neighborhoods.loc[0, 'Neighborhood']

u'Wakefield'

Get the neighborhood's latitude and longitude values.

In [15]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.8947051766, -73.8472005205.


#### Now, let's get the top 100 venues that are in Wakefield.

First, let's create the GET request URL. Name your URL **url**.

In [16]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

#radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude,  
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=RH2TN4WWZYPCFZ3SWLLPJUECHOYUBPGFCL05JVGXPIBEMMNT&client_secret=ZMCVBIQCF0110IUVFTSD4BIJCE43M4GSA21ZKSSMH3X0YH3K&v=20180605&ll=40.8947051766,-73.8472005205&limit=100'

Send the GET request and examine the resutls

In [17]:
results = requests.get(url).json()
#results

In [18]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [19]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat        lng
0          Lollipops Gelato          Dessert Shop  40.894123 -73.845892
1        Ripe Kitchen & Bar  Caribbean Restaurant  40.898152 -73.838875
2           Ali's Roti Shop  Caribbean Restaurant  40.894036 -73.856935
3                   Jimbo's          Burger Joint  40.891740 -73.858226
4  Kingston Tropical Bakery                Bakery  40.888568 -73.859885

And how many categories were returned by Foursquare?

In [20]:
#print('{} venues were returned by Foursquare.'.format(nearby_venues.groupby['categories'].shape[0]))

catg_df = nearby_venues.groupby('categories').count()

In [21]:
catg_df

name  lat  lng
categories                            
American Restaurant        2    2    2
Arcade                     1    1    1
Asian Restaurant           1    1    1
Automotive Shop            1    1    1
Bagel Shop                 1    1    1
Bakery                     5    5    5
Bank                       1    1    1
Bar                        4    4    4
Breakfast Spot             1    1    1
Burger Joint               1    1    1
Caribbean Restaurant      14   14   14
Cocktail Bar               1    1    1
Convenience Store          1    1    1
Deli / Bodega              3    3    3
Dessert Shop               1    1    1
Diner                      4    4    4
Discount Store             3    3    3
Donut Shop                 5    5    5
Fast Food Restaurant       3    3    3
Food Truck                 1    1    1
Furniture / Home Store     1    1    1
Gas Station                1    1    1
Grocery Store              2    2    2
Gym / Fitness Center       1    1    1
Historic Site              1    1    1
Ice Cream Shop             3    3    3
Indian Restaurant          1    1    1
Italian Restaurant         5    5    5
Kitchen Supply Store       1    1    1
Mobile Phone Shop          2    2    2
Nightclub                  1    1    1
Pharmacy                   6    6    6
Pizza Place                6    6    6
Pub                        3    3    3
Rental Car Location        1    1    1
Restaurant                 1    1    1
Sandwich Place             1    1    1
Seafood Restaurant         2    2    2
Shipping Store             1    1    1
Soup Place                 1    1    1
Spa                        1    1    1
Sports Bar                 1    1    1
Supermarket                2    2    2
Supplement Shop            1    1    1

And how many venues were returned by Foursquare?

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in New York

#### Let's create a function to repeat the same process to all the neighborhoods in NY

In [26]:
def getNearbyVenues(names, latitudes, longitudes):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            LIMIT)
            
        # make the GET request
        try:
            responce = requests.get(url).json()
            results = responce["response"]['groups'][0]['items']
        except:
            print(responce)
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [27]:
NYC_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### Let's check the size of the resulting dataframe

In [28]:
print(NYC_venues.shape)
NYC_venues.head()

(30346, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                      Venue  Venue Latitude  Venue Longitude  \
0          Lollipops Gelato       40.894123       -73.845892   
1        Ripe Kitchen & Bar       40.898152       -73.838875   
2           Ali's Roti Shop       40.894036       -73.856935   
3                   Jimbo's       40.891740       -73.858226   
4  Kingston Tropical Bakery       40.888568       -73.859885   

         Venue Category  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3          Burger Joint  
4                Bakery

Let's check how many venues were returned for each neighborhood

In [29]:
NYC_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                     100                     100   
Annadale                                      60                      60   
Arden Heights                                100                     100   
Arlington                                    100                     100   
Arrochar                                     100                     100   
Arverne                                      100                     100   
Astoria                                      100                     100   
Astoria Heights                              100                     100   
Auburndale                                   100                     100   
Bath Beach                                    93                      93   
Battery Park City                            100                     100   
Bay Ridge                                    100                     100   
Bay Terrace                                  200                     200   
Baychester                                   100                     100   
Bayside                                      100                     100   
Bayswater                                    100                     100   
Bedford Park                                 100                     100   
Bedford Stuyvesant                           100                     100   
Beechhurst                                   100                     100   
Bellaire                                     100                     100   
Belle Harbor                                 100                     100   
Bellerose                                    100                     100   
Belmont                                      100                     100   
Bensonhurst                                  100                     100   
Bergen Beach                                 100                     100   
Blissville                                   100                     100   
Bloomfield                                   100                     100   
Boerum Hill                                  100                     100   
Borough Park                                 100                     100   
Breezy Point                                 100                     100   
Briarwood                                    100                     100   
Brighton Beach                               100                     100   
Broad Channel                                100                     100   
Broadway Junction                            100                     100   
Bronxdale                                    100                     100   
Brooklyn Heights                             100                     100   
Brookville                                   100                     100   
Brownsville                                  100                     100   
Bulls Head                                   100                     100   
Bushwick                                     100                     100   
Butler Manor                                 100                     100   
Cambria Heights                              100                     100   
Canarsie                                     100                     100   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                  100                     100   
Castleton Corners                            100                     100   
Central Harlem                               100                     100   
Charleston                                   100                     100   
Chelsea                                      200                     200   
Chinatown                                    100                     100   

### Check number of neighborhoods returned from Foursquare Database

In [30]:
len(NYC_venues.groupby('Neighborhood').count())

302

#### Let's find out how many unique categories can be curated from all the returned venues

In [31]:
print('There are {} uniques categories.'.format(len(NYC_venues['Venue Category'].unique())))

There are 457 uniques categories.


#### Let's save returned venues data not to traffic foursquare API each time

In [32]:
NYC_venues.to_csv(index=False, path_or_buf='NYC_venues_data.csv', sep=',', header=True, encoding = 'utf-8')

<a id='item3'></a>

## 3. Analyze NYC Neighborhoods

In [33]:
# one hot encoding
NYC_onehot = pd.get_dummies(NYC_venues[['Venue Category']], prefix="", prefix_sep="")

# drop neighborhood column
NYC_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)

# add neighborhood column back to dataframe
NYC_onehot.insert(0, 'Neighborhood', NYC_venues['Neighborhood'])

NYC_onehot.head(5)

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield                  0               0                  0   
1    Wakefield                  0               0                  0   
2    Wakefield                  0               0                  0   
3    Wakefield                  0               0                  0   
4    Wakefield                  0               0                  0   

   African Restaurant  Airport Food Court  Airport Lounge  Airport Service  \
0                   0                   0               0                0   
1                   0                   0               0                0   
2                   0                   0               0                0   
3                   0                   0               0                0   
4                   0                   0               0                0   

   Airport Terminal  American Restaurant  Animal Shelter  Antique Shop  \
0                 0                    0               0             0   
1                 0                    0               0             0   
2                 0                    0               0             0   
3                 0                    0               0             0   
4                 0                    0               0             0   

   Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0         0       0                 0                       0            0   
1         0       0                 0                       0            0   
2         0       0                 0                       0            0   
3         0       0                 0                       0            0   
4         0       0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Dealership  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0                0                0          0           0           0   
1                0                0          0           0           0   
2                0                0          0           0           0   
3                0                0          0           0           0   
4                0                0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       1     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Beer Bar  Beer Garden  \
0                   0           0      0          0         0            0   
1                   0           0      0          0         0            0   
2                   0           0      0          0         0            0   
3               

And let's examine the new dataframe size.

In [34]:
NYC_onehot.shape

(30346, 457)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [35]:
NYC_grouped = NYC_onehot.groupby('Neighborhood').mean().reset_index()
NYC_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.020000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.010000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.000000            0.00   
13                  Baychester           0.010000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.000000            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.010000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.000000            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57              

#### Let's confirm the new size

In [36]:
NYC_grouped.shape

(302, 457)

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [37]:
# set number of clusters
kclusters = 10

NYC_grouped_clustering = NYC_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(NYC_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 1, 8, 4, 2, 9, 2, 0])

In [38]:
NYC_grouped.shape

(302, 457)

In [39]:
len(kmeans.labels_)

302

Let's create a new dataframe that includes the cluster

In [40]:
NYC_merged = NYC_grouped[['Neighborhood']]

# add clustering labels
NYC_merged.insert(1, 'Cluster Labels', kmeans.labels_)

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
NYC_merged = NYC_merged.join(neighborhoods.set_index('Neighborhood'), on='Neighborhood')

NYC_merged.head() # check the last columns!

Neighborhood  Cluster Labels        Borough   Latitude  Longitude
0       Allerton               0          Bronx  40.865788 -73.859319
1       Annadale               0  Staten Island  40.538114 -74.178549
2  Arden Heights               0  Staten Island  40.549286 -74.185887
3      Arlington               1  Staten Island  40.635325 -74.165104
4       Arrochar               8  Staten Island  40.596313 -74.067124

Finally, let's visualize the resulting clusters

In [41]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(NYC_merged['Latitude'], NYC_merged['Longitude'], NYC_merged['Neighborhood'], NYC_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)

folium.Marker([Downtown_lat, Downtown_long], popup='Downtown, Brooklyn', icon=folium.Icon(color='red')).add_to(map_clusters)      

map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Get Downtown, Brooklyn Cluster and define new data frame for this cluster

In [42]:
NYC_merged[NYC_merged['Neighborhood']=='Downtown']

Neighborhood  Cluster Labels   Borough   Latitude  Longitude
73     Downtown               2  Brooklyn  40.690844 -73.983463

In [107]:
cluster = NYC_merged[NYC_merged['Neighborhood']=='Downtown']['Cluster Labels'].iloc[0]
print('Downtown, Brooklyn cluster = ' + str(cluster))

Downtown, Brooklyn cluster = 2


#### Cluster 1

In [108]:
similar_neighborhoods = NYC_merged.loc[NYC_merged['Cluster Labels'] == cluster].reset_index()
similar_neighborhoods.drop(['index'], axis=1, inplace=True)
similar_neighborhoods

Neighborhood  Cluster Labels    Borough   Latitude  Longitude
0           Astoria               2     Queens  40.768509 -73.915654
1        Auburndale               2     Queens  40.761730 -73.791762
2         Bay Ridge               2   Brooklyn  40.625801 -74.030621
3           Bayside               2     Queens  40.766041 -73.774274
4       Boerum Hill               2   Brooklyn  40.685683 -73.983748
5     Carnegie Hill               2  Manhattan  40.782683 -73.953256
6         Chinatown               2  Manhattan  40.715618 -73.994279
7      Civic Center               2  Manhattan  40.715229 -74.005415
8           Clinton               2  Manhattan  40.759101 -73.996119
9        Douglaston               2     Queens  40.766846 -73.742498
10         Downtown               2   Brooklyn  40.690844 -73.983463
11         Elmhurst               2     Queens  40.744049 -73.881656
12         Flatiron               2  Manhattan  40.739673 -73.990947
13         Flushing               2     Queens  40.764454 -73.831773
14     Forest Hills               2     Queens  40.725264 -73.844475
15  Jackson Heights               2     Queens  40.751981 -73.882821
16       Lenox Hill               2  Manhattan  40.768113 -73.958860
17   Lincoln Square               2  Manhattan  40.773529 -73.985338
18     Little Italy               2  Manhattan  40.719324 -73.997305
19      Little Neck               2     Queens  40.770826 -73.738898
20          Midtown               2  Manhattan  40.754691 -73.981669
21    Midtown South               2  Manhattan  40.748510 -73.988713
22      Murray Hill               2  Manhattan  40.748303 -73.978332
23      Murray Hill               2     Queens  40.764126 -73.812763
24             Noho               2  Manhattan  40.723259 -73.988434
25       North Side               2   Brooklyn  40.714823 -73.958809
26  Oakland Gardens               2     Queens  40.745619 -73.754950
27       Park Slope               2   Brooklyn  40.672321 -73.977050
28  Queensboro Hill               2     Queens  40.744572 -73.825809
29      Sunset Park               2   Brooklyn  40.645103 -74.010316
30     Sutton Place               2  Manhattan  40.760280 -73.963556
31          Tribeca               2  Manhattan  40.721522 -74.010683
32       Tudor City               2  Manhattan  40.746917 -73.971219
33       Turtle Bay               2  Manhattan  40.752042 -73.967708
34  Upper East Side               2  Manhattan  40.775639 -73.960508
35  Upper West Side               2  Manhattan  40.787658 -73.977059
36     West Village               2  Manhattan  40.734434 -74.006180
37       Whitestone               2     Queens  40.781291 -73.814202
38         Woodside               2     Queens  40.746349 -73.901842

In [109]:
print('There is ' + str(similar_neighborhoods.shape[0]) + ' neighborhoods similar to Downtown, Brooklyn in New York')

There is 39 neighborhoods similar to Downtown, Brooklyn in New York


### Let's sort these similar set of neighborhoods using Foursquare API to pick the least neighborhood that has this kind of venues category (Bakery)

#### I'll not use the same data I received from foursquare API at above (NYC_venues) which sure it contains Venue Category of Bakery, because of 2 reasons:
#### 1- Foursquare request limited to 100 venues although i specified limit more than 100 
#### 2- Collected venues are the top and the nearest to the neighborhood Coordinates provided during request.

In [112]:
Bakery_categoryId = '4bf58dd8d48988d16a941735' # From Foursquare API Documentation

def getNearbyBakery(Neighborhoods, Boroughs, latitudes, longitudes, LIMIT=50, Radius=400):
    
    Bakery_venues_list=[]
    for Neighborhood, Borough, lat, lng in zip(Neighborhoods, Boroughs, latitudes, longitudes):
        address = Neighborhood + ', ' + Borough
        print(address)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&near={}&limit={}&radius={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            address,  
            LIMIT,
            Radius,
            Bakery_categoryId)
        
        # make the GET request
        try:
            responce = requests.get(url).json()
            Bakery_results = responce["response"]['groups'][0]['items']
        except:
            # create the API request URL
            print(responce)
            print(address)
            url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&limit={}&radius={}&categoryId={}'.format(
                CLIENT_ID, 
                CLIENT_SECRET, 
                VERSION, 
                lat, 
                lng,
                LIMIT,
                Radius,
                Bakery_categoryId)
            responce = requests.get(url).json()
            Bakery_results = responce["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        #print(Bakery_results[0]['venue']['categories'][0]['name'])
        Bakery_venues_list.append([(
            Neighborhood, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            #v['venue']['categories'][0]['name']
        ) for v in Bakery_results])

    nearby_bakery = pd.DataFrame([item for Bakery_venues_list in Bakery_venues_list for item in Bakery_venues_list])
    nearby_bakery.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude'#, 
                  #'Venue Category'
                            ]
    
    return(nearby_bakery)

In [113]:
Bakery_venues = getNearbyBakery(Neighborhoods=similar_neighborhoods['Neighborhood'],
                                Boroughs=similar_neighborhoods['Borough'],
                                latitudes=similar_neighborhoods['Latitude'],
                                longitudes=similar_neighborhoods['Longitude']
                               )

Astoria, Queens
Auburndale, Queens
{u'meta': {u'errorType': u'failed_geocode', u'code': 400, u'requestId': u'5e23767bc94979001be1ee44', u'errorDetail': u"Couldn't geocode param near: Auburndale, Queens"}, u'response': {}}
Auburndale, Queens
Bay Ridge, Brooklyn
Bayside, Queens
Boerum Hill, Brooklyn
Carnegie Hill, Manhattan
Chinatown, Manhattan
Civic Center, Manhattan
Clinton, Manhattan
{u'meta': {u'errorType': u'failed_geocode', u'code': 400, u'requestId': u'5e2376a147b43d00232131d1', u'errorDetail': u"Couldn't geocode param near: Clinton, Manhattan"}, u'response': {}}
Clinton, Manhattan
Douglaston, Queens
Downtown, Brooklyn
Elmhurst, Queens
Flatiron, Manhattan
{u'meta': {u'errorType': u'failed_geocode', u'code': 400, u'requestId': u'5e23762c882fc7001b99aa5c', u'errorDetail': u"Couldn't geocode param near: Flatiron, Manhattan"}, u'response': {}}
Flatiron, Manhattan
Flushing, Queens
Forest Hills, Queens
Jackson Heights, Queens
Lenox Hill, Manhattan
{u'meta': {u'errorType': u'failed_geoco

#### Let's check the size of the resulting dataframe

In [114]:
print(Bakery_venues.shape)
Bakery_venues.head(20)

(1012, 6)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       Astoria              40.768509              -73.915654   
1       Astoria              40.768509              -73.915654   
2       Astoria              40.768509              -73.915654   
3       Astoria              40.768509              -73.915654   
4       Astoria              40.768509              -73.915654   
5       Astoria              40.768509              -73.915654   
6       Astoria              40.768509              -73.915654   
7       Astoria              40.768509              -73.915654   
8       Astoria              40.768509              -73.915654   
9       Astoria              40.768509              -73.915654   
10      Astoria              40.768509              -73.915654   
11      Astoria              40.768509              -73.915654   
12      Astoria              40.768509              -73.915654   
13      Astoria              40.768509              -73.915654   
14      Astoria              40.768509              -73.915654   
15      Astoria              40.768509              -73.915654   
16      Astoria              40.768509              -73.915654   
17      Astoria              40.768509              -73.915654   
18      Astoria              40.768509              -73.915654   
19      Astoria              40.768509              -73.915654   

                              Venue  Venue Latitude  Venue Longitude  
0                  Titan Foods Inc.       40.769198       -73.919253  
1                 Il Fornaio Bakery       40.767518       -73.922828  
2              New York Bakery Café       40.766443       -73.920341  
3     Leli's Bakery and Pastry Shop       40.765132       -73.917696  
4            Parisi Brothers Bakery       40.762054       -73.925484  
5                     Yaya's Bakery       40.767401       -73.921044  
6                  Artopolis Bakery       40.773816       -73.913670  
7       Brooklyn Bagel & Coffee Co.       40.764732       -73.916944  
8                       Bakeway NYC       40.767753       -73.923245  
9                       Bakeway NYC       40.763113       -73.927667  
10                      Omonia Cafe       40.761219       -73.923949  
11                   Baskin-Robbins       40.766778       -73.920629  
12                   Vaccaro Bakery       40.765264       -73.913832  
13  Aloria Cakes and Gourmet Sweets       40.772149       -73.927909  
14                       Néo Bakery       40.765979       -73.919384  
15                 Omonia Next Door       40.761369       -73.924064  
16              La Sabrosura Bakery       40.765700       -73.919061  
17                   Zakir's Bakery       40.770137       -73.918945  
18                   Astoria Bakers       40.765891       -73.919283  
19                Mac Donuts Bakery       40.764726       -73.940112

Let's check how many venues were returned for each neighborhood

In [115]:
Bakery_venues.groupby('Neighborhood').count()['Venue']

Neighborhood
Astoria            33
Bay Ridge          50
Bayside            12
Boerum Hill        24
Carnegie Hill      15
Chinatown          50
Civic Center       50
Clinton             7
Douglaston         27
Downtown           13
Elmhurst           10
Flatiron           31
Flushing           50
Forest Hills       15
Jackson Heights    50
Lenox Hill         11
Lincoln Square     32
Little Italy       50
Little Neck        25
Midtown            29
Midtown South      34
Murray Hill        66
Noho               50
North Side         15
Oakland Gardens    26
Park Slope          8
Queensboro Hill     2
Sunset Park        50
Sutton Place       16
Tribeca            20
Tudor City         50
Turtle Bay          5
Upper East Side     8
Upper West Side    18
West Village       22
Whitestone          5
Woodside           33
Name: Venue, dtype: int64

#### Let's exclude Bakery dataframe and sort data ascending

In [116]:
Neighborhood_Bakery = pd.DataFrame(Bakery_venues.groupby('Neighborhood').count()['Venue'],index=None).reset_index()
Neighborhood_Bakery = Neighborhood_Bakery.rename(columns={'Venue': 'Bakery_Count'})
Neighborhood_Bakery.head(10)

Neighborhood  Bakery_Count
0        Astoria            33
1      Bay Ridge            50
2        Bayside            12
3    Boerum Hill            24
4  Carnegie Hill            15
5      Chinatown            50
6   Civic Center            50
7        Clinton             7
8     Douglaston            27
9       Downtown            13

In [117]:
similar_neighborhoods = similar_neighborhoods.join(Neighborhood_Bakery.set_index('Neighborhood'), on='Neighborhood')
similar_neighborhoods.sort_values("Bakery_Count", axis = 0, ascending = True, inplace = True, na_position ='last')

In [118]:
similar_neighborhoods.head(5)

Neighborhood  Cluster Labels    Borough   Latitude  Longitude  \
28  Queensboro Hill               2     Queens  40.744572 -73.825809   
33       Turtle Bay               2  Manhattan  40.752042 -73.967708   
37       Whitestone               2     Queens  40.781291 -73.814202   
8           Clinton               2  Manhattan  40.759101 -73.996119   
27       Park Slope               2   Brooklyn  40.672321 -73.977050   

    Bakery_Count  
28           2.0  
33           5.0  
37           5.0  
8            7.0  
27           8.0

<a id='item6'></a>

## 6. Final Result

Map the least 5 neighborhood has Bakery venues

In [119]:
# create map of Astoria using latitude and longitude values
map_branch = folium.Map(location=[latitude, longitude], zoom_start=11)

# First Branch Neighborhood
folium.Marker([Downtown_lat, Downtown_long], popup='Downtown, Brooklyn', icon=folium.Icon(color='red')).add_to(map_branch)      

# Second Branch Neighborhoods
for lat, lng, name, count in zip(similar_neighborhoods['Latitude'].iloc[0:5], similar_neighborhoods['Longitude'].iloc[0:5], similar_neighborhoods['Neighborhood'].iloc[0:5], similar_neighborhoods['Bakery_Count'].iloc[0:5]):
    label = name
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=20,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_branch) 

    folium.map.Marker(
        [lat, lng],
        icon=folium.features.DivIcon(
            icon_size=(0,0),
            icon_anchor=(5,15),
            html='<div style="font-size: 16pt">%s</div>' % int(count),
            )
    ).add_to(map_branch)
map_branch